In [1]:
import robin_stocks.robinhood as rh
import pandas as pd
import requests
from datetime import datetime
import yfinance as yf
import time 
import math
import random

username ='liuweiwang0824@gmail.com'
password ='Umcqar45&M'

def login():
    rh.login(username, password)


login()

def open_market():
    time_now = datetime.now().time()
    market_open = datetime.time(9, 30, 0)
    market_close = datetime.time(15, 59, 0)
    return market_open < time_now < market_close

def get_cash():
    rh.login(username, password)
    rh_profile = rh.load_account_profile()
    return float(rh_profile['portfolio_cash'])
print(f'Buying power before making trade: {get_cash()}')

def get_holdings_and_bought_price(stocks):
    holdings = {stock: 0 for stock in stocks}
    bought_price = {stock: 0 for stock in stocks}
    rh_holdings = rh.account.build_holdings()
    for stock in stocks:
        holdings[stock] = int(float((rh_holdings.get(stock, {}).get('quantity', '0'))))
        bought_price[stock] = float((rh_holdings.get(stock, {}).get('average_buy_price', '0')))
    return holdings, bought_price

today = datetime.today()
a, b, c = str(today.year), str(today.month), str(today.day)

f1 = pd.read_csv(r'\\DESKTOP-RRDK2EH\Server\Users\jizha\Desktop\seabridge_datapool1\final_strategy_data_temporaly\\three_strategy_buy_point_' + a + '_' + b + '_' + c + '.csv')
# 移除带有点（"."）的股票代码
ticker_sum = f1['0'].tolist()

ticker_sum = [ticker for ticker in ticker_sum if "." not in ticker]
#ticker_sum.remove('RTWG.L')
#ticker_sum.remove('PPHC.L')
print(f"Total stock in pool: {len(ticker_sum)}")
 

def buy(stock, allowable_holdings):
    rh.orders.order_buy_fractional_by_price(stock, allowable_holdings, timeInForce='gfd', extendedHours=False)
 
def get_yahoo_historical_prices_5min(stock):
    data = yf.download(stock, interval='5m', period='2d', progress=False)
    if len(data) < 3:  # Ensure we have enough data points
        return None, None, None, None
    current_price = data['Close'].iloc[-1]  # Last data point
    price_5min = data['Close'].iloc[-2]  # Second last data point
    price_10min = data['Close'].iloc[-3]  # Third last data point
    
    # Extracting the previous day's close
    yesterday_data = data[data.index.date != data.index[-1].date()]
    close_p = yesterday_data['Close'].iloc[-1] if not yesterday_data.empty else None

    return current_price, price_5min, price_10min, close_p
def final_trade_stock_data(stocks):
    final_data = {}
    
    for stock in stocks:
        current_price, price_5min, price_10min, close_p = get_yahoo_historical_prices_5min(stock)
        if current_price is None or price_5min is None or price_10min is None or close_p is None:
            continue
        
        # Check if the stock meets the criteria
        if price_5min > price_10min and current_price > close_p:
            pct_change = ((current_price - close_p) / close_p) * 100
            if 0 < pct_change <5:
                final_data[stock] = {
                    'current_price': current_price,
                    'price_5min': price_5min,
                    'price_10min': price_10min,
                    'close_p': close_p,
                    'pct_change': pct_change
                }
    
    return final_data


selected_stocks = final_trade_stock_data(ticker_sum)

print(f"Selected stocks: {len(selected_stocks)}")
for stock, data in selected_stocks.items():
    print(f"{stock}:")
    print(f"  5-min price: ${data['price_5min']:.2f}")
    print(f"  10-min price: ${data['price_10min']:.2f}")
    print(f"  Previous close price: ${data['close_p']:.2f}")
    print(f"  Percentage change: {data['pct_change']:.2f}%")


def calculate_multiplicative_factor(change):
#    """根据市场变化计算乘法因子。"""
    return 40 + 40 * abs(change) / 0.03
    
def calculate_market_activity_coefficient(total_stocks, selected_stocks):
    """计算市场活跃度系数"""
    ratio = selected_stocks / total_stocks
    market_activity_coefficient = 0.6 / (1 + math.exp(-12 * (ratio - 0.5))) + 0.2
    market_activity_coefficient=round(market_activity_coefficient,2)

    return market_activity_coefficient
 
def calculate_total_buying_power(change, cash, total_stocks, selected_stocks):
    market_activity_coefficient = calculate_market_activity_coefficient(total_stocks, selected_stocks)
    print(f"Stock Pool Activity Coefficient: {market_activity_coefficient}")  # 打印市场活跃系数

    multiplicative_factor = calculate_multiplicative_factor(change)
    multiplicative_factor=round(multiplicative_factor)
    print(f"Multiplicative Factor: {multiplicative_factor}")  # 打印乘法因子

    adjustment_coefficient = 1 + change * multiplicative_factor
    total_buying_power_adjusted = adjustment_coefficient * cash * market_activity_coefficient
    total_buying_power_adjusted = max(0, total_buying_power_adjusted)
    if total_buying_power_adjusted > cash:
        total_buying_power_adjusted = cash
    
    return total_buying_power_adjusted

stocks = final_trade_stock_data(ticker_sum)
num_of_stocks = len(stocks)
print(f"Today's stock pick contains {num_of_stocks} stocks:")
def get_stock_change(stock):
    # 使用yfinance获取股票的最近两天的收盘价格
    data = yf.download(stock, period="2d", progress=False)['Close']
    if len(data) < 2:
        return None, None
    today_close, yesterday_close = data[-1], data[-2]
    change_percentage = (today_close - yesterday_close) / yesterday_close * 100
    return today_close, change_percentage

# 修改打印股票信息的部分：
for stock in stocks:
    current_price, change_pct = get_stock_change(stock)
    if current_price is None or change_pct is None:
        print(f"{stock}: Data not available")
        continue
    #print(f"{stock}: Current Price: ${current_price:.2f}, Change: {change_pct:.2f}%")

spy_current = yf.download("SPY", period="1d", progress=False)['Close'][-1]
qqq_current = yf.download("QQQ", period="1d", progress=False)['Close'][-1]
spy_previous_close = yf.download("SPY", period="2d", progress=False)['Close'][-2]
qqq_previous_close = yf.download("QQQ", period="2d", progress=False)['Close'][-2]
spy_change = (spy_current - spy_previous_close) / spy_previous_close
qqq_change = (qqq_current - qqq_previous_close) / qqq_previous_close
average_change = (spy_change + qqq_change)  

#print(f"SPY Change: {spy_change*100:.2f}%")
#print(f"QQQ Change: {qqq_change*100:.2f}%")
print(f"Market Optimism Factor: {average_change*100:.2f}")  # 打印SPY和QQQ的涨跌百分比

stocks = final_trade_stock_data(ticker_sum)

myCash = get_cash()
cash = calculate_total_buying_power(average_change, myCash, len(ticker_sum), len(stocks))
cash = round(cash) - 1
print('Buying power:')
print(cash)
if cash <= 0:
    print("Insufficient buying power. No trades will be executed.")
else:
 
    trade_dict = {stock: 0 for stock in stocks}
    price_dict = {stock: 0 for stock in stocks}
    df_trades = pd.DataFrame(columns=stocks)
    df_prices = pd.DataFrame(columns=stocks)

    #prices = rh.stocks.get_latest_price(stocks)
    holdings, bought_price = get_holdings_and_bought_price(stocks)
    # Modify the check_purchase_successful function to check the holdings directly
    def check_purchase_successful(stock):
        holdings_after_purchase, _ = get_holdings_and_bought_price([stock])
        return holdings_after_purchase[stock] > 0  # Check if we hold any of the stock

    for stock in stocks:
        allowable_holdings = round(cash / len(stocks), 1)
        print(f"Attempting to buy {stock}:")
        print(f"Funds allocated: ${allowable_holdings}")

        # Place the market order
        buy(stock, allowable_holdings)

        # Pause for 3 seconds to allow the broker to process the order
        time_to_sleep = random.uniform(5, 12)
                                
        time.sleep(time_to_sleep)

        # Check if purchase was successful
    #    attempts = 1
    #    while not check_purchase_successful(stock) and attempts < 1:  # Limit to 2 attempts
    #        print(f"Purchase of {stock} failed. Retrying...")
    #        buy(stock, allowable_holdings)

            # Pause for 3 seconds again
    #        time.sleep(3)

    #        attempts += 1

     #   if attempts == 1:
     #       print(f"Failed to buy {stock} after 1 attempt.")


    #-----------#
    time.sleep(time_to_sleep)

    print(f'Buying power after making trade: {get_cash()}')


#ToolBox
#quantity = 11.11 # convert quantity to float once
#s='A'   
#rh.orders.order_sell_market(symbol=s, quantity=quantity, timeInForce='gfd')
    

Buying power before making trade: 29297.64


FileNotFoundError: [Errno 2] No such file or directory: '\\\\DESKTOP-RRDK2EH\\Server\\Users\\jizha\\Desktop\\seabridge_datapool1\\final_strategy_data_temporaly\\\\three_strategy_buy_point_2024_7_23.csv'

In [ ]:
import random
import robin_stocks.robinhood as rh
import pandas as pd
import time as time_module

# User credentials
 
username ='liuweiwang0824@gmail.com'
password ='Umcqar45&M'


def login():
    rh.login(username, password)

def sell_positions_less_than_one_share():
    my_stocks = rh.build_holdings()  # 获取当前所有持仓
    df = pd.DataFrame(my_stocks).T

    for index, row in df.iterrows():
        quantity = float(row['quantity'])
        if quantity < 1:
            try:
                print(f"Attempting to sell {quantity} shares of {index}")
                response = rh.orders.order_sell_market(symbol=index, quantity=str(quantity), timeInForce='gfd')
                print(f"Sold {quantity} shares of {index}")
                time_to_sleep = random.uniform(6, 10)
                time_module.sleep(time_to_sleep)
            except Exception as e:
                print(f"Error selling {index}: {e}")

# Log in to Robinhood
login()

# Continuously sell positions less than one share with a random interval of 6-10 seconds
while True:
    print("Starting to sell positions with less than one share...")
    sell_positions_less_than_one_share()
    print("Finished selling positions with less than one share. Sleeping for 10 seconds before next check...")
    time_module.sleep(100000)  # Wait for 10 seconds before checking again


Starting to sell positions with less than one share...
Attempting to sell 0.24 shares of CAG
Sold 0.24 shares of CAG
Finished selling positions with less than one share. Sleeping for 10 seconds before next check...
Starting to sell positions with less than one share...
401 Client Error: Unauthorized for url: https://api.robinhood.com/positions/?nonzero=true
401 Client Error: Unauthorized for url: https://api.robinhood.com/portfolios/
401 Client Error: Unauthorized for url: https://api.robinhood.com/accounts/
Finished selling positions with less than one share. Sleeping for 10 seconds before next check...
Starting to sell positions with less than one share...
401 Client Error: Unauthorized for url: https://api.robinhood.com/positions/?nonzero=true
401 Client Error: Unauthorized for url: https://api.robinhood.com/portfolios/
401 Client Error: Unauthorized for url: https://api.robinhood.com/accounts/
Finished selling positions with less than one share. Sleeping for 10 seconds before next 

In [ ]:
 
username ='liuweiwang0824@gmail.com'
password ='Umcqar45&M'
 
import random

import pytz
from datetime import timedelta
import math
import robin_stocks.robinhood as rh
import pandas as pd
import requests
from datetime import datetime
import time as time_module
from robin_stocks.orders import order_sell_stop_loss
def login():
    rh.login(username, password)
def get_stop(stock):# pivotpoints
        from datetime import datetime as dt
        import datetime
        import dateutil
        today = datetime.datetime.today()
        delta = dateutil.relativedelta.relativedelta(months=1)
        end = (today-datetime.timedelta(1)).strftime('%Y-%m-%d')
        start = (today - delta).strftime('%Y-%m-%d')

        import requests
        api_key = '86dd63f6b8ae774b061232685b78eb52'
        from datetime import datetime
        bs = requests.get(f'https://financialmodelingprep.com/api/v3/historical-price-full/{stock}?from={start}&to={end}&apikey={api_key}').json()['historical']
       
        # Print the raw data to check
        #print(f"Raw data for {stock}:")
       # print(bs)
       
        stock = pd.DataFrame(bs)
        stock =stock[['date','open','high','low','close','volume']]
        stock = stock.rename(columns = {'date':'Date', 'open':'Open', 'high':'High','low':'Low', 'close':'Close', 'volume':'volume'})
        stock = stock.set_index('Date')
        stock= stock.sort_index()
        last_day = stock.iloc[-1].to_frame().T
        not_pivots = last_day.columns
        last_day['center_gravity'] = (last_day['High'] + last_day['Low'] + last_day['Close'])/3
        last_day['center_gravity']=round(last_day['center_gravity'],2)
        # Print calculations
        #print("\nCalculations:")
      #  print(f"Center of Gravity: {last_day['center_gravity'].values[0]}")
       
        last_day['vol_up1'] = 2*last_day['center_gravity'] - last_day['Low']
        last_day['vol_up1']=round(last_day['vol_up1'],2)
      #  print(f"Volatility Up 1: {last_day['vol_up1'].values[0]}")
       
        last_day['vol_down1'] = 2*last_day['center_gravity'] - last_day['High']
        last_day['vol_down1']=round(last_day['vol_down1'],2)
       # print(f"Volatility Down 1: {last_day['vol_down1'].values[0]}")
       
        last_day['vol_up2'] = last_day['center_gravity'] + (last_day['High'] - last_day['Low'])
        last_day['vol_up2']=round(last_day['vol_up2'],2)
      #  print(f"Volatility Up 2: {last_day['vol_up2'].values[0]}")
      #  
        last_day['vol_down2'] = last_day['center_gravity'] - (last_day['High'] - last_day['Low'])
        last_day['vol_down2']=round(last_day['vol_down2'],2)
       # print(f"Volatility Down 2: {last_day['vol_down2'].values[0]}")
       
        last_day['vol_up3'] = last_day['center_gravity'] + 2*(last_day['High'] - last_day['Low'])
        last_day['vol_up3']=round(last_day['vol_up3'],2)
        #print(f"Volatility Up 3: {last_day['vol_up3'].values[0]}")
       
        last_day['vol_down3'] = last_day['center_gravity'] - 2*(last_day['High'] - last_day['Low'])
        last_day['vol_down3']=round(last_day['vol_down3'],2)
        #print(f"Volatility Down 3: {last_day['vol_down3'].values[0]}")
       
        last_day['stop_loss'] = (last_day['vol_down2'] + last_day['vol_down3'])/2
        last_day['stop_loss']=round(last_day['stop_loss'],2)
        #print(f"Initial Stop Loss: {last_day['stop_loss'].values[0]}")
       
        last_day['stop_loss_pct'] = (last_day['Close'] - last_day['stop_loss'])/last_day['Close']*100
        last_day['stop_loss_pct']=round(last_day['stop_loss_pct'],2)
       # print(f"Initial Stop Loss Percentage: {last_day['stop_loss_pct'].values[0]}%")
       
        if last_day['stop_loss_pct'][-1] >3.5:
            last_day['stop_loss'][-1]= (last_day['vol_down1'][-1] + last_day['Close'][-1])/2
           # print(f"Adjusted Stop Loss (because percentage > 3.5%): {last_day['stop_loss'].values[0]}")
       
        return last_day

from pandas.tseries.holiday import USFederalHolidayCalendar
from datetime import time as datetime_time
def open_market():
    # Check if today is a weekend or holiday
    today = datetime.now().date()
    cal = USFederalHolidayCalendar()
    holidays = cal.holidays(start=today, end=today)
   
    if today.weekday() >= 5 or today in holidays:
        return False

    # Check if the current time is within trading hours
    time_now = datetime.now().time()
    market_open = datetime_time(9,30,0) # 9:30AM
    market_close = datetime_time(15,59,0) # 3:59PM

    if time_now > market_open and time_now < market_close:
        return True
    else:
        return False
 
def get_trailing_stop_percentage(stock):
#    print(f"Entering get_trailing_stop_percentage for {stock}...")
    stop_price = get_stop(stock)['stop_loss'][0]
    stop_price=round(stop_price,2)
    current_price = all_data1['price'][stock]
    trailing_percentage = (current_price - stop_price) / current_price
   
    # Print statements for debugging
    print(f"\nStock: {stock}")
    print(f"Current Price: ${current_price}")
    print(f"Stop Price from get_stop(): ${stop_price}")
    print(f"Trailing Percentage (from difference): {trailing_percentage*100:.2f}%")
#    print(f"Exiting get_trailing_stop_percentage for {stock}...")
   
    return trailing_percentage * 0.2  # Use 20% of the calculated stop percentage

def cancel_all_orders():
    open_orders = rh.orders.get_all_open_stock_orders()
    if not open_orders:  # Check if open_orders is None or empty
        print("No open orders found.")
        return
    for order in open_orders:
        if order:  # Check if the order is not None
            try:
                rh.orders.cancel_stock_order(order['id'])
                # Wait for a random time between 5 and 10 seconds
                time_to_sleep1 = random.uniform(5, 10)
                time_module.sleep(time_to_sleep1)
            except Exception as e:
                print(f"Error canceling order for {order['id']}: {e}")
        else:
            print("Found a None order.")

login()

sold_half = set()  # Track stocks that we have sold half of

while True:
    # Check if the market is open
    if open_market():
        print("Market is open.")

       
        cancel_all_orders()
        my_stocks = rh.build_holdings()
        df = pd.DataFrame(my_stocks).T
        df1 = df[['price', 'quantity', 'average_buy_price', 'percent_change']]
        stock = df1.index.tolist()
        all_data = pd.DataFrame()
   
        for ticker in stock:
            try:
                last_day = get_stop(ticker)
                last_day.index = [ticker]  
                all_data = pd.concat([all_data, last_day], axis=0)
            except Exception as e:
                print(f"Error processing stock {ticker}: {e}")
                if hasattr(e, 'response') and hasattr(e.response, 'text'):
                    print(e.response.text)
   
   
        all_data = all_data[['stop_loss']]
        all_data1 = df1.merge(all_data, left_index=True, right_index=True)
        all_data1['price'] = all_data1['price'].astype(float)
        all_data1['pct_cha'] = ((all_data1['price'] - all_data1['stop_loss']) / all_data1['price']) * 100
   
        x = random.random()
        y = float((x + 5) / 100)
        z = float((10 - x) / 100)
        all_data1['average_buy_price'] = all_data1['average_buy_price'].astype(float)
        all_data1['target_price1'] = all_data1['average_buy_price'] * (1 + y)
        all_data1['target_price1']=round(all_data1['target_price1'],2)
        all_data1['target_price2'] = all_data1['average_buy_price'] * (1 + z)
        all_data1['target_price2']=round(all_data1['target_price2'],2)
    #    print(all_data1)
   
        print("Starting the loop to process each stock for trailing stop...")

   
        for s in all_data1.index.tolist():
            current_price = all_data1['price'][s]
            average_price = all_data1['average_buy_price'][s]
            quantity = float(all_data1['quantity'][s])
            quantity0 = round(quantity, 4)
            quantity_to_sell=math.floor(quantity)
   
            trailing_stop_pct = get_trailing_stop_percentage(s)
            trailing_stop_price = current_price * (1 - trailing_stop_pct)
            loss_pct = (current_price - trailing_stop_price) / current_price * 100
            gain_pct = (current_price - average_price) / average_price * 100
   
            if all_data1['target_price1'][s] >= current_price:
                stopPrice_value = float(all_data1['stop_loss'][s])
                stopPrice_value = round(stopPrice_value, 2)
                limitPrice_value = stopPrice_value - 0.5  # 设置限价为“停止价格减去0.5”
                print(f"Symbol: {s}, Quantity: {quantity}, Stop Price: {stopPrice_value}, Limit Price: {limitPrice_value}")
            
                if quantity_to_sell >= 1:  # 添加这行检查
                    try:
                        response = rh.order(symbol=s, side='sell', stopPrice=str(stopPrice_value), limitPrice=str(limitPrice_value), quantity=str(quantity_to_sell), timeInForce='gtc')                
                        time_to_sleep = random.uniform(15, 30)
                        time_module.sleep(time_to_sleep)
                    except Exception as e:
                        print(f"Error executing order for {s}: {e}")
                        if hasattr(e, 'response'):
                            print("Error response:", e.response.text)
                            if hasattr(e.response, 'json'):
                                try:
                                    error_json = e.response.json()
                                    print("Error JSON:", error_json)
                                except:
                                    pass
                else:
                    print(f"Skipping order for {s} because quantity to sell is less than 1.")  # 添加这行输出
            
                print(f"First target price not yet reached for {s}, setting stop loss order.")
                print(f"Current Price: ${current_price:.2f}, Target Price 1: ${all_data1['target_price1'][s]:.2f}")
            
               
            elif current_price >= all_data1['target_price1'][s] and s not in sold_half:
                    if quantity0 >= 2:
                            quantity1 = math.ceil(quantity0 / 2)  # sell half
                            quantity1 = math.floor(quantity1)
                            try:
                                response = rh.orders.order_sell_market(symbol=s, quantity=quantity1, timeInForce='gfd')
                                time_to_sleep = random.uniform(15, 30)
                                time_module.sleep(time_to_sleep)
                            except Exception as e:
                                print(f"Error executing order for {s}: {e}")
                                if hasattr(e, 'response'):
                                    print("Error response:", e.response.text)
                                    if hasattr(e.response, 'json'):
                                        try:
                                            error_json = e.response.json()
                                            print("Error JSON:", error_json)
                                        except:
                                            pass
                            print(f"First target price reached for {s}, setting stop loss order for half at ${trailing_stop_price:.2f}.")
                            print(f"Current Price: ${current_price:.2f}, Target Price 1: ${all_data1['target_price1'][s]:.2f}")
                            sold_half.add(s)  # Add the stock to the sold half set
   
                    else:
                            try:
                                response = rh.orders.order_sell_market(symbol=s, quantity=quantity, timeInForce='gfd')
                                time_to_sleep = random.uniform(15, 30)
                                time_module.sleep(time_to_sleep)
                            except Exception as e:
                                print(f"Error executing order for {s}: {e}")
                                if hasattr(e, 'response'):
                                    print("Error response:", e.response.text)
                                    if hasattr(e.response, 'json'):
                                        try:
                                            error_json = e.response.json()
                                            print("Error JSON:", error_json)
                                        except:
                                            pass
                            print(f"First target price reached for {s}, Current Price: ${current_price:.2f}, with a gain of {gain_pct:.2f}%.")
                            print(f"Due to low initial funding, the entire position in this stock has been sold for profit.")
   
   
            elif current_price >= all_data1['target_price2'][s]:    
                if quantity > 1:
                    sell_amount = math.floor(quantity)
                    try:
                        response = rh.order(symbol=s, side='sell', stopPrice=str(trailing_stop_price), limitPrice=str(trailing_stop_price-0.2), quantity=str(sell_amount), timeInForce='gtc')
                        time_to_sleep = random.uniform(15, 30)
                        time_module.sleep(time_to_sleep)
                    except Exception as e:
                        print(f"Error executing order for {s}: {e}")
                        if hasattr(e, 'response'):
                            print("Error response:", e.response.text)
                            if hasattr(e.response, 'json'):
                                try:
                                    error_json = e.response.json()
                                    print("Error JSON:", error_json)
                                except:
                                    pass
                    print(f"Second target price reached for {s}, setting stop loss order for all at ${trailing_stop_price:.2f} with a gain of {gain_pct:.2f}%.")
                    print(f"Current Price: ${current_price:.2f}, Target Price 2: ${all_data1['target_price2'][s]:.2f}, Average Buy Price: ${average_price:.2f}")
   
                else:
                    try:
                        response = rh.orders.order_sell_market(symbol=s, quantity=quantity, timeInForce='gfd')
                        time_to_sleep = random.uniform(15, 30)
                        time_module.sleep(time_to_sleep)
                       
                    except Exception as e:
                        print(f"Error executing order for {s}: {e}")
                        if hasattr(e, 'response'):
                            print("Error response:", e.response.text)
                            if hasattr(e.response, 'json'):
                                try:
                                    error_json = e.response.json()
                                    print("Error JSON:", error_json)
                                except:
                                    pass
                               
                    print(f"Second target price reached for {s}, Current Price: ${current_price:.2f} with a gain of {gain_pct:.2f}%.")
                    print(f"Due to low initial funding, the entire position in this stock has been sold for profit.")
   
   
   
   
            elif current_price <= trailing_stop_price:
                try:
                    response = rh.orders.order_sell_market(symbol=s, quantity=quantity, timeInForce='gfd')
                    time_to_sleep = random.uniform(15, 30)

                    time_module.sleep(time_to_sleep)

                   
                except Exception as e:
                    print(f"Error executing order for {s}: {e}")
                    if hasattr(e, 'response'):
                        print("Error response:", e.response.text)
                        if hasattr(e.response, 'json'):
                            try:
                                error_json = e.response.json()
                                print("Error JSON:", error_json)
                            except:
                                pass
                           
                print(f"Trailing stop would be triggered for {s}, close for all at ${trailing_stop_price:.2f}. ")
                print(f"Current Price: ${current_price:.2f}, Trailing Stop Price: ${trailing_stop_price:.2f}")
   
        print("Ending main loop iteration...")
        time_module.sleep(18000)  # Wait for an hour before checking again

    # else:
    #     print("Market is closed. Waiting for an hour before checking again.")
    #     time_module.sleep(7200)  # Wait for an hour before checking again
           
    else:
       print("Market is closed or it's past 3:30 PM ET. Waiting until 10:00 AM ET to start again.")
       
       # Calculate the number of seconds to wait until 10:00 AM ET the next day
       current_datetime_eastern = datetime.now(pytz.timezone('US/Eastern'))
       next_start_time = current_datetime_eastern.replace(hour=10, minute=0, second=0, microsecond=0) + timedelta(days=1)
       wait_seconds = (next_start_time - current_datetime_eastern).seconds
       
       time_module.sleep(wait_seconds)